In [128]:
#!/Users/jim/anaconda3/envs/sb/bin/python

import pandas as pd
import numpy as np
from datetime import datetime as dt
from sklearn.linear_model import LinearRegression
import plotly.express as px

In [112]:
pga = pd.read_csv('~/dev/sb/data/pga_stats.csv')

In [113]:
pga['event_completed'] = pd.to_datetime(pga.event_completed)
pga['event_year'] = pga.event_completed.dt.year
pga.set_index('event_completed',inplace=True)

In [114]:
pga['2Y_sg'] = pga.groupby('dg_id')['sg_total'].transform(lambda d: d.rolling('720D', min_periods=1).mean())
pga['2M_sg'] = pga.groupby('dg_id')['sg_total'].transform(lambda d: d.rolling('60D', min_periods=1).mean())
pga = pga.reset_index()
pga['strokes_up_down'] = pga.score - pga.course_par

In [115]:
events = pga[['season','event_name','event_completed']].drop_duplicates().sort_values(by=['season','event_completed'],ascending=True)
events['event_order'] = events.groupby('season')['event_completed'].cumcount()+1

event_dummy = pga[['season','event_id','course_name','round']].drop_duplicates()
event_dummy['event_dummy'] = event_dummy.groupby(['season','event_id','course_name'])['round'].cumcount()+1
event_dummy.drop_duplicates()

base = pd.merge(pga,events[['season','event_name','event_order']],how='left',on=['season','event_name'])
base = pd.merge(base,event_dummy[['season','event_id','course_name','round','event_dummy']],how='left',on=['season','event_id','course_name','round'])
base_no_na = base.loc[base.score.isna()==False].copy()

In [160]:
contin_predictors = ['2Y_sg','2M_sg']
dummy_predictors = ['dg_id','event_id']
response = ['score']
dummies = pd.get_dummies(base_no_na[dummy_predictors],drop_first=True)
base_no_na = pd.concat([base_no_na,dummies],axis=1)
base_no_na.dtypes

event_completed      datetime64[ns]
event_id                      int64
event_name                   object
season                        int64
sg_categories                object
tour                         object
traditional_stats            object
year                          int64
dg_id                         int64
fin_text                     object
player_name                  object
round                         int64
course_name                  object
course_num                    int64
course_par                    int64
driving_acc                 float64
driving_dist                float64
gir                         float64
great_shots                 float64
poor_shots                  float64
prox_fw                     float64
prox_rgh                    float64
score                       float64
scrambling                  float64
sg_app                      float64
sg_arg                      float64
sg_ott                      float64
sg_putt                     

In [152]:
train = base_no_na.loc[base_no_na.event_completed < dt.strptime('2023-01-01','%Y-%m-%d')].copy()
test = base_no_na.loc[base_no_na.event_completed >= dt.strptime('2023-01-01','%Y-%m-%d')].copy()
X, y = train[predictors], train[response]
skm = LinearRegression()
skm.fit(X,y)
print(f"""model
        intercept={skm.intercept_[0]:,.2f}
        dg_id_coeff={skm.coef_[0][0]:,.3f}
        2Y_sg_coeff={skm.coef_[0][1]:,.3f}
        2M_sg_coeff={skm.coef_[0][2]:,.3f}
        R2={skm.score(X,y):,.2%}""")
test['predicted_score'] = skm.predict(test[predictors])
train['predicted_score'] = skm.predict(train[predictors])
test['resid'] , train['resid'] = test.predicted_score - test.score, train.predicted_score - train.score

model
        intercept=70.80
        dg_id_coeff=-0.000
        2Y_sg_coeff=-0.050
        2M_sg_coeff=-0.993
        R2=19.59%


In [153]:
px.scatter(train,x="event_id",y="resid")

In [126]:
X = base[['dg_id','event_dummy']].loc[base.score.isna()==False]
Y = base[['score']].loc[base.score.isna()==False]
# ols = lm.LinearRegression()
# ols.fit(X,Y)
# print(ols.coef_)

In [162]:
pd.get_dummies(data=pga,columns=['season','event_id','course_name','round']).shape

(124771, 257)